In [27]:
import math
import json
import numpy as np
import pandas as pd
import geopandas as gpd
from datetime import timedelta
from bokeh.io import show, output_notebook
from bokeh.plotting import figure
from bokeh.layouts import column, row, widgetbox
from bokeh.palettes import brewer
from bokeh.models import (NumeralTickFormatter, CDSView, ColorBar, ColumnDataSource,
                          CustomJS, CustomJSFilter, 
                          GeoJSONDataSource, HoverTool,
                          LinearColorMapper, LogColorMapper, Slider)
from bokeh.models.formatters import DatetimeTickFormatter

output_notebook()

Loading BokehJS ...

In [28]:
df = pd.read_csv('../data/covid-19-data/us-counties.csv', parse_dates=["date"], index_col='date')
df.tail()

county    state     fips  cases  deaths
date                                                   
2020-04-12    Sublette  Wyoming  56035.0      1       0
2020-04-12  Sweetwater  Wyoming  56037.0      7       0
2020-04-12       Teton  Wyoming  56039.0     56       0
2020-04-12       Uinta  Wyoming  56041.0      4       0
2020-04-12    Washakie  Wyoming  56043.0      4       0

In [29]:
df.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 53848 entries, 2020-01-21 to 2020-04-12
Data columns (total 5 columns):
county    53848 non-null object
state     53848 non-null object
fips      53132 non-null float64
cases     53848 non-null int64
deaths    53848 non-null int64
dtypes: float64(1), int64(2), object(2)
memory usage: 2.5+ MB


In [30]:
df_ca = df.where(df['state'] == 'California')
df_ca = df_ca.dropna()
df_ca.head()

county       state    fips  cases  deaths
date                                                      
2020-01-25       Orange  California  6059.0    1.0     0.0
2020-01-26  Los Angeles  California  6037.0    1.0     0.0
2020-01-26       Orange  California  6059.0    1.0     0.0
2020-01-27  Los Angeles  California  6037.0    1.0     0.0
2020-01-27       Orange  California  6059.0    1.0     0.0

In [31]:
df_ca['cases'].sum()

258559.0

In [32]:
df_ca['deaths'].sum()

6314.0

In [33]:
df_ca['total'] = df_ca['cases'].cumsum()

In [34]:
df_ca.head()

county       state    fips  cases  deaths  total
date                                                             
2020-01-25       Orange  California  6059.0    1.0     0.0    1.0
2020-01-26  Los Angeles  California  6037.0    1.0     0.0    2.0
2020-01-26       Orange  California  6059.0    1.0     0.0    3.0
2020-01-27  Los Angeles  California  6037.0    1.0     0.0    4.0
2020-01-27       Orange  California  6059.0    1.0     0.0    5.0

In [35]:
df_counties = df_ca[['county', 'fips', 'cases', 'deaths']].groupby(['county']).sum()
df_counties.head()

fips    cases  deaths
county                              
Alameda    258043.0  10249.0   217.0
Alpine      84042.0     21.0     0.0
Amador     144120.0     52.0     0.0
Butte      138161.0    194.0     0.0
Calaveras  120180.0     87.0     0.0

In [36]:
ca_counties_shapefile = gpd.read_file('../data/CA_Counties/CA_Counties_TIGER2016.shp')
ca_counties_shapefile.head()

STATEFP COUNTYFP  COUNTYNS  GEOID           NAME              NAMELSAD LSAD  \
0      06      091  00277310  06091         Sierra         Sierra County   06   
1      06      067  00277298  06067     Sacramento     Sacramento County   06   
2      06      083  00277306  06083  Santa Barbara  Santa Barbara County   06   
3      06      009  01675885  06009      Calaveras      Calaveras County   06   
4      06      111  00277320  06111        Ventura        Ventura County   06   

  CLASSFP  MTFCC CSAFP CBSAFP METDIVFP FUNCSTAT       ALAND      AWATER  \
0      H1  G4020  None   None     None        A  2468694587    23299110   
1      H1  G4020   472  40900     None        A  2499183617    76073827   
2      H1  G4020  None  42200     None        A  7084000598  2729814515   
3      H1  G4020  None   None     None        A  2641820834    43806026   
4      H1  G4020   348  37100     None        A  4773390489   945942791   

      INTPTLAT      INTPTLON  \
0  +39.5769252  -120.5219926   
1  +38.4500114  -121.3404409   
2  +34.5370572  -120.0399729   
3  +38.1838996  -120.5614415   
4  +34.3587415  -119.1331432   

                                            geometry  
0  POLYGON ((-13431319.75097945 4821511.426395644...  
1  POLYGON ((-13490651.47641084 4680831.603393857...  
2  (POLYGON ((-13423116.77225655 4042044.14856006...  
3  POLYGON ((-13428575.483353 4627725.227535474, ...  
4  (POLYGON ((-13317853.59433417 3931602.41399276...

In [37]:
# Merge shapefile with population data
counties = ca_counties_shapefile.merge(df_counties, left_on='NAME', right_on='county')
counties.head()

STATEFP COUNTYFP  COUNTYNS  GEOID           NAME              NAMELSAD LSAD  \
0      06      067  00277298  06067     Sacramento     Sacramento County   06   
1      06      083  00277306  06083  Santa Barbara  Santa Barbara County   06   
2      06      009  01675885  06009      Calaveras      Calaveras County   06   
3      06      111  00277320  06111        Ventura        Ventura County   06   
4      06      037  00277283  06037    Los Angeles    Los Angeles County   06   

  CLASSFP  MTFCC CSAFP  ... METDIVFP FUNCSTAT        ALAND      AWATER  \
0      H1  G4020   472  ...     None        A   2499183617    76073827   
1      H1  G4020  None  ...     None        A   7084000598  2729814515   
2      H1  G4020  None  ...     None        A   2641820834    43806026   
3      H1  G4020   348  ...     None        A   4773390489   945942791   
4      H1  G4020   348  ...    31084        A  10510651024  1794730436   

      INTPTLAT      INTPTLON  \
0  +38.4500114  -121.3404409   
1  +34.5370572  -120.0399729   
2  +38.1838996  -120.5614415   
3  +34.3587415  -119.1331432   
4  +34.1963983  -118.2618616   

                                            geometry      fips    cases  \
0  POLYGON ((-13490651.47641084 4680831.603393857...  315484.0   7937.0   
1  (POLYGON ((-13423116.77225655 4042044.14856006...  176407.0   2940.0   
2  POLYGON ((-13428575.483353 4627725.227535474, ...  120180.0     87.0   
3  (POLYGON ((-13317853.59433417 3931602.41399276...  207774.0   3769.0   
4  (POLYGON ((-13210018.38774803 3958856.14118129...  470886.0  94780.0   

   deaths  
0   289.0  
1    19.0  
2     0.0  
3   109.0  
4  2288.0  

[5 rows x 21 columns]

In [38]:
# Input GeoJSON source that contains features for plotting
geosource = GeoJSONDataSource(geojson=counties.to_json())

In [39]:
# Define color palettes
palette = brewer['Reds'][8]
palette = palette[::-1] # reverse order of colors so higher values have darker colors

# Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
color_mapper = LinearColorMapper(palette=palette, low=0, high=1000)

# Create color bar.
color_bar = ColorBar(color_mapper=color_mapper, 
                     label_standoff=8,
                     width=500, height=20,
                     border_line_color=None,
                     location=(0,0), 
                     orientation='horizontal',
                    )

# Create figure object.
p = figure(title='Covid-19 cases', 
           plot_height = 950, plot_width = 900, 
           toolbar_location = 'below',
           tools='pan, wheel_zoom, box_zoom, reset')

p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None

# Add patch renderer to figure.
counties = p.patches('xs', 'ys', source=geosource,
                   fill_color = {'field' :'cases',
                                 'transform' : color_mapper},
                   line_color = 'black', 
                   line_width = 0.25, 
                   fill_alpha = 1)
# Create hover tool
p.add_tools(HoverTool(renderers = [counties],
                      tooltips = [('County','@NAME'),
                                  ('Cases', '@cases'),
                                  ('Deaths', '@deaths'),
                                 ]))
# Specify layout
p.add_layout(color_bar, 'below')
show(p)